# Colab Demo

## Dependencies and Imports

In [1]:
#@title Install dependencies

!pip install -q torchaudio omegaconf

import torch
from pprint import pprint
from omegaconf import OmegaConf
from IPython.display import Audio, display

torch.hub.download_url_to_file('https://raw.githubusercontent.com/snakers4/silero-models/master/models.yml',
                               'latest_silero_models.yml',
                               progress=False)
models = OmegaConf.load('latest_silero_models.yml')

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.5/79.5 kB 1.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.0/117.0 kB 4.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done


## List models

In [2]:
# see latest avaiable models
available_languages = list(models.tts_models.keys())
print(f'Available languages {available_languages}')

for lang in available_languages:
    _models = list(models.tts_models.get(lang).keys())
    print(f'Available models for {lang}: {_models}')

Available languages ['ru', 'en', 'de', 'es', 'fr', 'ba', 'xal', 'tt', 'uz', 'ua', 'indic', 'multi']
Available models for ru: ['v3_1_ru', 'ru_v3', 'aidar_v2', 'aidar_8khz', 'aidar_16khz', 'baya_v2', 'baya_8khz', 'baya_16khz', 'irina_v2', 'irina_8khz', 'irina_16khz', 'kseniya_v2', 'kseniya_8khz', 'kseniya_16khz', 'natasha_v2', 'natasha_8khz', 'natasha_16khz', 'ruslan_v2', 'ruslan_8khz', 'ruslan_16khz']
Available models for en: ['v3_en', 'v3_en_indic', 'lj_v2', 'lj_8khz', 'lj_16khz']
Available models for de: ['v3_de', 'thorsten_v2', 'thorsten_8khz', 'thorsten_16khz']
Available models for es: ['v3_es', 'tux_v2', 'tux_8khz', 'tux_16khz']
Available models for fr: ['v3_fr', 'gilles_v2', 'gilles_8khz', 'gilles_16khz']
Available models for ba: ['aigul_v2']
Available models for xal: ['v3_xal', 'erdni_v2']
Available models for tt: ['v3_tt', 'dilyara_v2']
Available models for uz: ['v3_uz', 'dilnavoz_v2']
Available models for ua: ['v3_ua', 'mykyta_v2']
Available models for indic: ['v3_indic']
Avail

## V3

In [3]:
import torch

language = 'ru'
model_id = 'v3_1_ru'
device = torch.device('cpu')

model, example_text = torch.hub.load(repo_or_dir='snakers4/silero-models',
                                     model='silero_tts',
                                     language=language,
                                     speaker=model_id)
model.to(device)  # gpu or cpu

/usr/local/lib/python3.10/dist-packages/torch/hub.py:286: UserWarning: You are about to download and run code from an untrusted repository. In a future release, this won't be allowed. To add the repository to your trusted list, change the command to {calling_fn}(..., trust_repo=False) and a command prompt will appear asking for an explicit confirmation of trust, or load(..., trust_repo=True), which will assume that the prompt is to be answered with 'yes'. You can also use load(..., trust_repo='check') which will only prompt for confirmation if the repo is not already trusted. This will eventually be the default behaviour
  warnings.warn(
Downloading: "https://github.com/snakers4/silero-models/zipball/master" to /root/.cache/torch/hub/master.zip
100%|██████████| 59.0M/59.0M [00:02<00:00, 21.1MB/s]


### Speakers

In [4]:
model.speakers

['aidar', 'baya', 'kseniya', 'xenia', 'eugene', 'random']

### Text

In [5]:
sample_rate = 48000
speaker = 'xenia'
put_accent=True
put_yo=True
example_text = 'В недрах тундры выдры в г+етрах т+ырят в вёдра ядра к+едров.'

audio = model.apply_tts(text=example_text,
                        speaker=speaker,
                        sample_rate=sample_rate,
                        put_accent=put_accent,
                        put_yo=put_yo)
print(example_text)
display(Audio(audio, rate=sample_rate))

В недрах тундры выдры в г+етрах т+ырят в вёдра ядра к+едров.


### SSML

In [6]:
ssml_sample = """
              <speak>
              <p>
                  Когда я просыпаюсь, <prosody rate="x-slow">я говорю довольно медленно</prosody>.
                  Пот+ом я начинаю говорить своим обычным голосом,
                  <prosody pitch="x-high"> а могу говорить тоном выше </prosody>,
                  или <prosody pitch="x-low">наоборот, ниже</prosody>.
                  Пот+ом, если повезет – <prosody rate="fast">я могу говорить и довольно быстро.</prosody>
                  А еще я умею делать паузы любой длины, например, две секунды <break time="2000ms"/>.
                  <p>
                    Также я умею делать паузы между параграфами.
                  </p>
                  <p>
                    <s>И также я умею делать паузы между предложениями</s>
                    <s>Вот например как сейчас</s>
                  </p>
              </p>
              </speak>
              """

sample_rate = 48000
speaker = 'xenia'
audio = model.apply_tts(ssml_text=ssml_sample,
                        speaker=speaker,
                        sample_rate=sample_rate)
display(Audio(audio, rate=sample_rate))

### Random speaker

#### Generate new

In [7]:
sample_rate = 48000
speaker = 'random'

example_text = 'В недрах тундры выдры в г+етрах т+ырят в вёдра ядра к+едров.'

audio = model.apply_tts(text=example_text,
                        speaker=speaker,
                        sample_rate=sample_rate)
print(example_text)
display(Audio(audio, rate=sample_rate))

Generated new voice
В недрах тундры выдры в г+етрах т+ырят в вёдра ядра к+едров.


#### Save generated speaker

In [8]:
voice_path = 'test_voice.pt'
model.save_random_voice(voice_path)

Saved generated voice to test_voice.pt


#### Generate with saved speaker

In [9]:
sample_rate = 48000
speaker = 'random'
voice_path = 'test_voice.pt'

example_text = 'В недрах тундры выдры в г+етрах т+ырят в вёдра ядра к+едров.'

audio = model.apply_tts(text=example_text,
                        speaker=speaker,
                        sample_rate=sample_rate,
                        voice_path=voice_path)
print(example_text)
display(Audio(audio, rate=sample_rate))

Loaded voice from test_voice.pt
В недрах тундры выдры в г+етрах т+ырят в вёдра ядра к+едров.


## V2

### One speaker

In [10]:
import torch

language = 'ru'
speaker = 'kseniya_v2'
sample_rate = 16000
device = torch.device('cpu')
model, example_text = torch.hub.load(repo_or_dir='snakers4/silero-models',
                                     model='silero_tts',
                                     language=language,
                                     speaker=speaker)
model.to(device)  # gpu or cpu

Using cache found in /root/.cache/torch/hub/snakers4_silero-models_master
100%|██████████| 132M/132M [00:05<00:00, 24.1MB/s]


In [11]:
audio = model.apply_tts(texts=[example_text],
                        sample_rate=sample_rate)

print(example_text)
display(Audio(audio[0], rate=sample_rate))

В н+едрах т+ундры в+ыдры в г+етрах т+ырят в в+ёдра +ядра к+едров.


### Multi speaker

In [12]:
import torch

language = 'multi'
speaker = 'multi_v2'
sample_rate = 16000
device = torch.device('cpu')
model, avail_speakers = torch.hub.load(repo_or_dir='snakers4/silero-models',
                                       model='silero_tts',
                                       language=language,
                                       speaker=speaker)
model.to(device)  # gpu or cpu

Using cache found in /root/.cache/torch/hub/snakers4_silero-models_master
100%|██████████| 130M/130M [00:05<00:00, 24.1MB/s]


In [13]:
speaker = 'dilyara'
example_text = avail_speakers['baya']['example']

In [14]:
audio = model.apply_tts(texts=[example_text],
                        speakers=[speaker],
                        sample_rate=sample_rate)

print(example_text)
display(Audio(audio[0], rate=sample_rate))

Съ+ешьте ещ+ё +этих м+ягких франц+узских б+улочек, д+а в+ыпейте ч+аю.


## V1

These examples are for older models and obsolete

In [15]:
import torch

language = 'ru'
speaker = 'kseniya_16khz'
device = torch.device('cpu')
model, symbols, sample_rate, example_text, apply_tts = torch.hub.load(repo_or_dir='snakers4/silero-models',
                                                                      model='silero_tts',
                                                                      language=language,
                                                                      speaker=speaker)
model = model.to(device)  # gpu or cpu

Using cache found in /root/.cache/torch/hub/snakers4_silero-models_master
100%|██████████| 136M/136M [00:06<00:00, 23.2MB/s]


In [16]:
audio = apply_tts(texts=[example_text],
                  model=model,
                  sample_rate=sample_rate,
                  symbols=symbols,
                  device=device)

print(example_text)
display(Audio(audio[0], rate=sample_rate))

В н+едрах т+ундры в+ыдры в г+етрах т+ырят в в+ёдра +ядра к+едров.


### Enhance synthesis with logmmse

In [17]:
!pip install -q logmmse

You can try to enhance synthesized audio with logmmse algorithm, though it could demand parameters tuning for the particular speaker.

In [18]:
import numpy as np
from logmmse import logmmse

enhanced = logmmse(np.array(audio[0]), sample_rate, output_file=None, initial_noise=1, window_size=160, noise_threshold=0.15)
display(Audio(enhanced, rate=sample_rate))

# Minimal Example to Run Locally

## Dependencies and Imports

In [19]:
#@title Install dependencies

!pip install -q torch==1.10

ERROR: Could not find a version that satisfies the requirement torch==1.10 (from versions: 1.11.0, 1.12.0, 1.12.1, 1.13.0, 1.13.1, 2.0.0, 2.0.1)
ERROR: No matching distribution found for torch==1.10


## V3

In [20]:
import os
import torch

device = torch.device('cpu')
torch.set_num_threads(4)
local_file = 'model.pt'

if not os.path.isfile(local_file):
    torch.hub.download_url_to_file('https://models.silero.ai/models/tts/ru/v3_1_ru.pt',
                                   local_file)

model = torch.package.PackageImporter(local_file).load_pickle("tts_models", "model")
model.to(device)

example_text = 'В недрах тундры выдры в г+етрах т+ырят в вёдра ядра кедров.'
sample_rate = 48000
speaker='baya'

audio_paths = model.save_wav(text=example_text,
                             speaker=speaker,
                             sample_rate=sample_rate)

100%|██████████| 59.0M/59.0M [00:02<00:00, 21.1MB/s]


## V2

### One speaker

In [22]:
import os
import torch

device = torch.device('cpu')
torch.set_num_threads(4)
local_file = 'model.pt'

if not os.path.isfile(local_file):
    torch.hub.download_url_to_file('https://models.silero.ai/models/tts/ru/v2_kseniya.pt',
                                   local_file)

model = torch.package.PackageImporter(local_file).load_pickle("tts_models", "model")
model.to(device)

example_batch = ['В недрах тундры выдры в г+етрах т+ырят в вёдра ядра кедров.',
                 'Котики - это жидкость!',
                 'М+ама М+илу м+ыла с м+ылом.']
sample_rate = 16000

audio_paths = model.save_wav(texts=example_batch,
                             sample_rate=sample_rate)
print(audio_paths)

TypeError: ignored

### Multi speaker

In [23]:
import os
import torch

device = torch.device('cpu')
torch.set_num_threads(4)
local_file = 'model_multi.pt'
speakers = ['aidar', 'baya', 'kseniya', 'irina', 'ruslan', 'natasha',
                    'thorsten', 'tux', 'gilles', 'lj', 'dilyara']

if not os.path.isfile(local_file):
    torch.hub.download_url_to_file('https://models.silero.ai/models/tts/multi/v2_multi.pt',
                                   local_file)

model = torch.package.PackageImporter(local_file).load_pickle("tts_models", "model")
model.to(device)

example_batch = ['В н+едрах т+ундры в+ыдры в г+етрах т+ырят в в+ёдра +ядра к+едров.',
                 'Fischers Fritze fischt frische Fische',
                 'Can you can a canned can into an un-canned can?']
example_speakers = ['baya', 'baya', 'baya']
sample_rate = 16000

audio_paths = model.save_wav(texts=example_batch,
                             speakers=example_speakers,
                             sample_rate=sample_rate)
print(audio_paths)

100%|██████████| 130M/130M [00:05<00:00, 24.0MB/s]


['test_000.wav', 'test_001.wav', 'test_002.wav']


## V1

We have received a lot of questions regarding the packaging requirements and utils from the `silero-models` repo from people trying to run models locally standalone (on their desktop for example). The project is packaged using `torch.hub` utils which basically are in the `hubconf.py` [file](https://github.com/snakers4/silero-models/blob/master/hubconf.py) and `tts_utils.py` [file](https://github.com/snakers4/silero-models/blob/master/src/silero/tts_utils.py).

For some reason this is very difficult to understand for some users. Also the `hubconf.py` contains some dependecies, which may not be necessarily required when running TTS for example on your desktop, i.e. `torchaudio` and `omegaconf`.

The following example is a minimal standalone example for such a use-case. It has very little external dependecies (essentially just `torch`, the rest is just standard python library). It basically does the following:

- Loads one of the 16 kHz models (I just chose one randomly), listed on the models.yml [file](https://github.com/snakers4/silero-models/blob/master/models.yml) locally and uses it as cache;
- The `symbols` are taken from the same  models.yml file;
- `apply_tts` is just one of the utils we provide in the project;
- The rest is self-explanatory;

In order to use this example, you will need to handle the resulting audios by yourself.

In [24]:
import os
import wave
import torch
import contextlib


torch.set_grad_enabled(False)
device = torch.device('cpu')
torch.set_num_threads(4)  # safe optimal value, i.e. 2 CPU cores, does not work properly in colab
symbols = '_~абвгдеёжзийклмнопрстуфхцчшщъыьэюя +.,!?…:;–'
local_file = 'model.jit'


if not os.path.isfile(local_file):
  torch.hub.download_url_to_file('https://models.silero.ai/models/tts/ru/v1_kseniya_16000.jit',
                                 local_file)

if not os.path.isfile('tts_utils.py'):
  torch.hub.download_url_to_file('https://raw.githubusercontent.com/snakers4/silero-models/master/src/silero/tts_utils.py',
                                 'tts_utils.py')
  from tts_utils import apply_tts  # modify these utils and use them your project


model = torch.jit.load('model.jit',
                       map_location=device)
model.eval()
example_batch = ['В н+едрах т+ундры в+ыдры в г+етрах т+ырят в в+ёдра +ядра к+едров.',
                 'К+отики - +это ж+идкость!',
                 'М+ама М+илу м+ыла с м+ылом.']
sample_rate = 16000
model = model.to(device)

audio = apply_tts(texts=example_batch,
                  model=model,
                  sample_rate=sample_rate,
                  symbols=symbols,
                  device=device)

def write_wave(path, audio, sample_rate):
    """Writes a .wav file.
    Takes path, PCM audio data, and sample rate.
    """
    with contextlib.closing(wave.open(path, 'wb')) as wf:
        wf.setnchannels(1)
        wf.setsampwidth(2)
        wf.setframerate(sample_rate)
        wf.writeframes(audio)

for i, _audio in enumerate(audio):
  write_wave(path=f'test_{str(i).zfill(3)}.wav',
             audio=(audio[i] * 32767).numpy().astype('int16'),
             sample_rate=16000)

100%|██████████| 136M/136M [00:05<00:00, 24.1MB/s]
100%|██████████| 3.02k/3.02k [00:00<00:00, 1.40MB/s]


In [25]:
from IPython.display import Audio, display
display(Audio('test_000.wav', rate=16000))
display(Audio('test_001.wav', rate=16000))
display(Audio('test_002.wav', rate=16000))